# Import library et data

In [3]:
import folium
import json
import numpy as np
import plotly.express as px
from folium.plugins import HeatMap
from folium import Choropleth, LayerControl, GeoJsonTooltip
import pandas as pd


In [2]:
nb_voitures = pd.read_csv("data/nb_voiture_annee_cdr.csv")
nb_voiture_commune = pd.read_csv("data/nb_voiture_commune.csv")
nb_voiture_dep = pd.read_csv("data/nb_voiture_dep.csv")
nb_voiture_reg = pd.read_csv("data/nb_voiture_reg.csv")
bornes_vehicules_dep = pd.read_csv("data/croisement_donnee_borne_voiture_departement.csv", encoding="utf-8")
bornes_vehicules_reg = pd.read_csv("data/croisement_donnee_borne_voiture_region.csv", encoding="utf-8")

bornes = pd.read_csv("data/bornes_completes.csv")
bornes2 = pd.read_csv("data/Bornes_nettoye2.csv", delimiter = ";")
population2 = pd.read_csv("data/population2.csv")
trafic_dep = pd.read_csv("data/tmja_dep_df.csv")
trafic_reg = pd.read_csv("data/tmja_reg.csv")

with open("data/communes.geojson", 'r') as f:
    geojson_data_com = json.load(f)

with open("data/france_departments.geojson", 'r') as f:
    geojson_data_dep = json.load(f)
with open("data/carte_interactive_avec_bornes.html", "r"   ) as file:
    carte_html = file.read()
with open("data/carte_tmja_troncons.html", "r"   ) as file:
    carte_html2 = file.read()

with open("data/regions.geojson", 'r') as f:
    geojson_data_reg = json.load(f)

C:\Users\MRH4\AppData\Local\Temp\ipykernel_29068\3401793680.py:1: DtypeWarning: Columns (0,5) have mixed types. Specify dtype option on import or set low_memory=False.
  nb_voitures = pd.read_csv("data/nb_voiture_annee_cdr.csv")
C:\Users\MRH4\AppData\Local\Temp\ipykernel_29068\3401793680.py:8: DtypeWarning: Columns (1,3) have mixed types. Specify dtype option on import or set low_memory=False.
  bornes = pd.read_csv("data/bornes_completes.csv")
C:\Users\MRH4\AppData\Local\Temp\ipykernel_29068\3401793680.py:9: DtypeWarning: Columns (18,19,20,21,22,23,24,29,33) have mixed types. Specify dtype option on import or set low_memory=False.
  bornes2 = pd.read_csv("data/Bornes_nettoye2.csv", delimiter = ";")


In [3]:
nb_voiture_dep = pd.read_csv("data/nb_voiture_annee_cdr.csv")
nb_voiture_dep["code_dep"] = nb_voiture_dep["code_dep"].astype(str)
nb_voiture_dep["code_dep"] = nb_voiture_dep["code_dep"].str.zfill(2)


C:\Users\MRH4\AppData\Local\Temp\ipykernel_29068\4058726969.py:1: DtypeWarning: Columns (0,5) have mixed types. Specify dtype option on import or set low_memory=False.
  nb_voiture_dep = pd.read_csv("data/nb_voiture_annee_cdr.csv")


In [4]:
nb_voiture_dep["annee"].unique()

array([2020, 2021, 2022, 2024, 2023], dtype=int64)

In [5]:
def create_map(nb_voiture_commune_dep, geojson_data,col_granu, info_carte):
    # Initialisation de la carte centrée sur la France
    map = folium.Map(location=[46.603354, 1.8883344], zoom_start=6, tiles='CartoDB positron')

    if info_carte == "nombre de véhicule":
        # Conversion des données en dictionnaire pour relier avec le GeoJSON
        col = 'nb_vp_rechargeables_el'
    elif info_carte == "ratio de véhicule électrique par rapport au total":
        # Conversion des données en dictionnaire pour relier avec le GeoJSON
        col = 'ratio_elec_total'

    vehicle_dict = nb_voiture_commune_dep.set_index(col_granu)[col].to_dict()
    # Mets les keys au format list str
    vehicle_dict = {str(k): v for k, v in vehicle_dict.items()}
    # Ajout des données au GeoJSON
    for feature in geojson_data['features']:
        feature_code = feature['properties']['code']
        feature['properties']['vehicles'] = vehicle_dict.get(feature_code, 'N/A')

    # Ajout d'un choropleth pour afficher les données
    folium.Choropleth(
        geo_data=geojson_data,
        name="Véhicules électriques par département",
        data=nb_voiture_commune_dep,
        columns=[col_granu, col],
        key_on='feature.properties.code',
        fill_color='YlGnBu',
        fill_opacity=0.7,
        line_opacity=0.05,
        legend_name="Nombre de véhicules électriques"
    ).add_to(map)
    # Ajout de tooltips interactifs
    folium.GeoJson(
        geojson_data,
        name="Détails",
        tooltip=folium.GeoJsonTooltip(
            fields=['code', 'nom', 'vehicles'],
            aliases=['Code :', 'Nom:', 'Véhicules électriques:']
        )
    ).add_to(map)

    # Ajout des contrôles de couches
    folium.LayerControl().add_to(map)
    
    return map
def create_map(nb_voiture_commune_dep, geojson_data, col_granu, selected_departement=None):
    # Filtrer les données par département si une sélection est faite
    if selected_departement:
        nb_voiture_commune_dep = nb_voiture_commune_dep[nb_voiture_commune_dep["code_dep"] == selected_departement]
    print(nb_voiture_commune_dep)
    
    # Initialisation de la carte centrée sur la France
    map = folium.Map(location=[46.603354, 1.8883344], zoom_start=6, tiles='CartoDB positron')

    # Créer un dictionnaire des valeurs des véhicules (nombre de véhicules électriques)
    col_nb_vp = 'nb_vp_rechargeables_el'
    vehicle_dict_nb_vp = nb_voiture_commune_dep.set_index(col_granu)[col_nb_vp].to_dict()
    vehicle_dict_nb_vp = {str(k): v for k, v in vehicle_dict_nb_vp.items()}
    print("Dictionnaire des valeurs (nombre de véhicules) :", vehicle_dict_nb_vp)

    # Créer un dictionnaire des valeurs des véhicules (ratio de véhicules électriques)
    col_ratio = 'ratio_elec_total'
    vehicle_dict_ratio = nb_voiture_commune_dep.set_index(col_granu)[col_ratio].to_dict()
    vehicle_dict_ratio = {str(k): v for k, v in vehicle_dict_ratio.items()}
    print("Dictionnaire des valeurs (ratio de véhicules) :", vehicle_dict_ratio)

    # Filtrer les features pour ne garder que celles ayant des données
    filtered_features = [
        {
            **feature,
            'properties': {
                **feature['properties'],
                'vehicles_nb': vehicle_dict_nb_vp.get(feature['properties']['code'], 'N/A'),
                'vehicles_ratio': vehicle_dict_ratio.get(feature['properties']['code'], 'N/A')
            }
        }
        for feature in geojson_data['features']
        if vehicle_dict_nb_vp.get(feature['properties']['code']) is not None or vehicle_dict_ratio.get(feature['properties']['code']) is not None
    ]
    
    # Créer un nouveau GeoJSON léger avec uniquement les communes sélectionnées
    filtered_geojson = {'type': 'FeatureCollection', 'features': filtered_features}
    taille = len(filtered_geojson["features"])
    print(f"Taille de features : {taille}")
    
    # Ajouter un Choropleth pour visualiser les données (nombre de véhicules)
    folium.Choropleth(
        geo_data=filtered_geojson,
        name="Nombre de véhicules électriques par département",
        data=nb_voiture_commune_dep,
        columns=[col_granu, col_nb_vp],
        key_on='feature.properties.code',
        fill_color='YlGnBu',
        fill_opacity=0.7,
        line_opacity=0.05,
        legend_name="Nombre de véhicules électriques"
    ).add_to(map)

    # Ajouter un Choropleth pour visualiser les données (ratio de véhicules)
    folium.Choropleth(
        geo_data=filtered_geojson,
        name="Ratio de véhicules électriques (%)",
        data=nb_voiture_commune_dep,
        columns=[col_granu, col_ratio],
        key_on='feature.properties.code',
        fill_color='YlGnBu',
        fill_opacity=0.7,
        line_opacity=0.05,
        legend_name="Ratio de véhicules électriques (%)"
    ).add_to(map)

    # Ajouter des tooltips pour afficher des informations
    folium.GeoJson(
        filtered_geojson,
        name="Détails",
        tooltip=folium.GeoJsonTooltip(
            fields=['code', 'nom', 'vehicles_nb', 'vehicles_ratio'],
            aliases=['Code :', 'Nom:', 'Véhicules électriques (nombre) :', 'Véhicules électriques (ratio %) :']
        )
    ).add_to(map)

    # Ajouter un contrôle des couches pour permettre de basculer entre les deux informations
    folium.LayerControl().add_to(map)
    
    return map




In [6]:
import os

geojson_data = geojson_data_com
info_carte = "nombre de véhicule"
years = [2020, 2021, 2022, 2023, 2024]
col_granu = "codgeo"
dataset = nb_voiture_dep

# Créer un répertoire pour sauvegarder les cartes si nécessaire
output_dir = "data/Carte_html"
os.makedirs(output_dir, exist_ok=True)

# Parcourir chaque année
for year in years:
    # Filtrer par année
    dataset_year = dataset[dataset["annee"] == year].copy()
    dataset_year.drop(columns=["annee"], inplace=True)

    # Calculer le ratio électrique en pourcentage
    dataset_year["ratio_elec_total"] = (
        dataset_year["nb_vp_rechargeables_el"] / dataset_year["nb_vp"]
    )
    dataset_year["ratio_elec_total"] = (dataset_year["ratio_elec_total"] * 100).round(2)

    # Parcourir chaque département
    for dep in dataset_year["code_dep"].unique():
        # Filtrer par département
        dataset_dep = dataset_year[dataset_year["code_dep"] == dep].copy()

        # Générer la carte pour le département
        map = create_map(dataset_dep, geojson_data, col_granu, dep)

        # Construire un nom de fichier explicite
        filename = f"carte_commune_{year}_{dep}.html"
        file_path = os.path.join(output_dir, filename)

        # Sauvegarder la carte
        map.save(file_path)
        print(f"Carte sauvegardée : {file_path}")


      codgeo                   libgeo  nb_vp_rechargeables_el  \
0      01001  L'ABERGEMENT-CLÉMENCIAT                       6   
4      01002    L'ABERGEMENT-DE-VAREY                       1   
18     01008                 AMBUTRIX                       5   
25     01010                ANGLEFORT                       5   
44     01015          ARBOYS EN BUGEY                       3   
...      ...                      ...                     ...   
23592   1454                 VIRIGNIN                       5   
23666   1456                  VONGNES                       0   
23696   1457                   VONNAS                      14   
32606   1997            NON IDENTIFIE                       0   
32611   1999                  FORAINS                       0   

       nb_vp_rechargeables_gaz  nb_vp code_dep nom_departement  code_region  \
0                            0    881       01             Ain           84   
4                            0    278       01             Ai

In [12]:
import folium
import os

def create_map(nb_voiture_commune_dep, geojson_data, col_granu, years, selected_departement=None):
    # Initialisation de la carte centrée sur la France
    map = folium.Map(location=[46.603354, 1.8883344], zoom_start=6, tiles='CartoDB positron')

    # Prendre Aude (11) comme département par défaut si aucun département sélectionné
    if not selected_departement:
        selected_departement = 11

    # Filtrer les données pour le département sélectionné
    nb_voiture_commune_dep_selected = nb_voiture_commune_dep[nb_voiture_commune_dep['code_dep'] == selected_departement]

    # Créer un dictionnaire des valeurs des véhicules (nombre de véhicules électriques)
    col_nb_vp = 'nb_vp_rechargeables_el'
    vehicle_dict_nb_vp = nb_voiture_commune_dep_selected.set_index(col_granu)[col_nb_vp].to_dict()
    vehicle_dict_nb_vp = {str(k): v for k, v in vehicle_dict_nb_vp.items()}

    # Créer un dictionnaire des valeurs des véhicules (ratio de véhicules électriques)
    col_ratio = 'ratio_elec_total'
    vehicle_dict_ratio = nb_voiture_commune_dep_selected.set_index(col_granu)[col_ratio].to_dict()
    vehicle_dict_ratio = {str(k): v for k, v in vehicle_dict_ratio.items()}

    # Filtrer les features pour ne garder que celles ayant des données
    filtered_features = [
        {
            **feature,
            'properties': {
                **feature['properties'],
                'vehicles_nb': vehicle_dict_nb_vp.get(feature['properties']['code'], 'N/A'),
                'vehicles_ratio': vehicle_dict_ratio.get(feature['properties']['code'], 'N/A')
            }
        }
        for feature in geojson_data['features']
        if vehicle_dict_nb_vp.get(feature['properties']['code']) is not None or vehicle_dict_ratio.get(feature['properties']['code']) is not None
    ]
    
    # Créer un nouveau GeoJSON léger avec uniquement les communes sélectionnées
    filtered_geojson = {'type': 'FeatureCollection', 'features': filtered_features}

    # Ajouter des tooltips pour afficher des informations
    folium.GeoJson(
        filtered_geojson,
        name="Détails",
        tooltip=folium.GeoJsonTooltip(
            fields=['code', 'nom', 'vehicles_nb', 'vehicles_ratio'],
            aliases=['Code :', 'Nom:', 'Véhicules électriques (nombre) :', 'Véhicules électriques (ratio %) :']
        )
    ).add_to(map)

    # Ajouter un contrôle des couches pour permettre de basculer entre les départements
    folium.LayerControl().add_to(map)
    
    # Ajouter un menu déroulant pour changer de département (liste des départements)
    departements = nb_voiture_commune_dep['code_dep'].unique()
    folium.map.CustomPane(name="departements_pane", z_index=490).add_to(map)
    for dep in departements:
        # Ajouter un layer par département
        dep_geojson = {
            'type': 'FeatureCollection',
            'features': [
                feature for feature in geojson_data['features']
                if feature['properties']['code'] == dep
            ]
        }

        folium.GeoJson(
            dep_geojson,
            name=f"Département {dep}",
            tooltip=folium.GeoJsonTooltip(
                fields=['code', 'nom', 'vehicles_nb', 'vehicles_ratio'],
                aliases=['Code :', 'Nom:', 'Véhicules électriques (nombre) :', 'Véhicules électriques (ratio %) :']
            )
        ).add_to(map)
        
    return map

# Exemple d'utilisation
geojson_data = geojson_data_com
info_carte = "nombre de véhicule"
years = [2020, 2021, 2022, 2023, 2024]
col_granu = "codgeo"
dataset = nb_voiture_dep
dataset["ratio_elec_total"] = (
    dataset["nb_vp_rechargeables_el"] / dataset["nb_vp"]
)
dataset["ratio_elec_total"] = (dataset["ratio_elec_total"] * 100).round(2)

# Créer un répertoire pour sauvegarder les cartes si nécessaire
output_dir = "data/Carte_html"
os.makedirs(output_dir, exist_ok=True)

# Créer la carte
map = create_map(dataset, geojson_data, col_granu, years, selected_departement=11)

# Sauvegarder la carte
file_path = os.path.join(output_dir, "carte_interactive.html")
map.save(file_path)
print(f"Carte sauvegardée : {file_path}")


AssertionError: The field code is not available in the data. Choose from: ().

In [13]:
for feature in geojson_data['features']:
    print(feature['properties'].keys())

dict_keys(['code', 'nom'])
dict_keys(['code', 'nom'])
dict_keys(['code', 'nom'])
dict_keys(['code', 'nom'])
dict_keys(['code', 'nom'])
dict_keys(['code', 'nom'])
dict_keys(['code', 'nom'])
dict_keys(['code', 'nom'])
dict_keys(['code', 'nom'])
dict_keys(['code', 'nom'])
dict_keys(['code', 'nom'])
dict_keys(['code', 'nom'])
dict_keys(['code', 'nom'])
dict_keys(['code', 'nom'])
dict_keys(['code', 'nom'])
dict_keys(['code', 'nom'])
dict_keys(['code', 'nom'])
dict_keys(['code', 'nom'])
dict_keys(['code', 'nom'])
dict_keys(['code', 'nom'])
dict_keys(['code', 'nom'])
dict_keys(['code', 'nom'])
dict_keys(['code', 'nom'])
dict_keys(['code', 'nom'])
dict_keys(['code', 'nom'])
dict_keys(['code', 'nom'])
dict_keys(['code', 'nom'])
dict_keys(['code', 'nom'])
dict_keys(['code', 'nom'])
dict_keys(['code', 'nom'])
dict_keys(['code', 'nom'])
dict_keys(['code', 'nom'])
dict_keys(['code', 'nom'])
dict_keys(['code', 'nom'])
dict_keys(['code', 'nom'])
dict_keys(['code', 'nom'])
dict_keys(['code', 'nom'])
d

In [1]:
import os
carte_html = {}
html_files = [f for f in os.listdir("data/Carte_html/") if f.endswith(".html")]
for html_file in html_files:
    file_path = os.path.join("data/Carte_html/", html_file)
    with open(file_path, "r") as file:
        carte_html[html_file] = file.read()

In [82]:
import webbrowser

map.save("data/Carte_html/carte_commune_2023_75.html")
webbrowser.open("C:\\Users\\MRH4\\OneDrive - MODEL RH\\Bureau\\Dossier_git\\data\\Carte_html\\carte_commune_2023_75.html")

True